In [2]:
import snake_sim as sim
import numpy as np
import G3C_extension as cga
import plotly.graph_objects as go
import pandas as pd

In [5]:
count = 5
length = 0.3
initial_configuration = sim.configuration_multilink_random_planar(count=count, length=length)
iterations = 300
dt = 0.01
T = np.arange(dt, iterations*dt+dt, dt)
# constant shift in x
dx = np.ones(iterations)*dt
# cos and sin in y and z
dy = np.cos(12*T)*dt
dz = -np.sin(20*T)*dt
configurations = sim.calculate_kinematics(initial_configuration, dx, dy, dz, iterations)

In [ ]:
still_configurations = [None] * len(configurations)
still_configurations[0] = configurations[0]
reverse_translations = [cga.translator(-dx[i]*cga.e1 - dy[i]*cga.e2 - dz[i]*cga.e3) for i in range(len(dx))]
for j, configuration in enumerate(configurations[1:], start=1):
    still_configuration = [None] * len(configuration)
    for i, pair in enumerate(configuration):
        still_pair = reverse_translations[j-1] * pair * ~reverse_translations[j-1]
        still_configuration[i] = still_pair
    still_configurations[j] = still_configuration

In [35]:
still_configurations[-2]

[(0.34486^e12) + (0.16874^e13) - (1.235^e14) - (0.96929^e15) + (0.00649^e23) - (0.42299^e24) - (0.54605^e25) - (0.18372^e34) - (0.24894^e35) + (0.76662^e45),
 (0.04657^e12) - (0.04627^e13) - (1.13534^e14) - (0.83593^e15) - (4e-05^e23) - (0.06998^e24) - (0.0831^e25) + (0.06856^e34) + (0.08185^e35) + (0.76978^e45),
 -(0.35629^e12) - (0.1114^e13) - (0.78203^e14) - (0.52673^e15) - (0.00915^e23) + (0.34296^e24) + (0.49509^e25) + (0.12732^e34) + (0.16833^e35) + (0.57964^e45),
 (0.22156^e12) + (0.22259^e13) - (0.67025^e14) - (0.41681^e15) - (0.00158^e23) - (0.15844^e24) - (0.27258^e25) - (0.16395^e34) - (0.27682^e35) + (0.52653^e45),
 (0.15092^e12) - (0.22365^e13) - (0.53398^e14) - (0.27016^e15) - (0.00328^e23) - (0.10838^e24) - (0.18559^e25) + (0.149^e34) + (0.26915^e35) + (0.46264^e45)]

In [33]:
sim.visualise_simulation_start_to_finish(still_configurations,)

TypeError: object of type 'NoneType' has no len()

In [ ]:
def visualise_simulation_animation_traces(
    configs_PP, ghost_count=1, delay=5, frame_duration=50
):
    """Plots the 3D animation of the snake robot."""
    configurations_dictionary = {
        0: cga.extract_points_for_scatter(cga.extract_unique_points(configs_PP[0]))
    }
    for i, config in enumerate(configs_PP, 1):
        iteration_points = cga.extract_unique_points(config)
        points_coordinates = cga.extract_points_for_scatter(iteration_points)
        configurations_dictionary[i] = points_coordinates

    configs_dataframe = pd.DataFrame(data=configurations_dictionary)

    first_pos = configs_dataframe[configs_dataframe.columns[0]]

    scatters = [
        go.Scatter3d(
            x=first_pos[0],
            y=first_pos[1],
            z=first_pos[2],
            marker=dict(color="blue", opacity=1),
            opacity=1,
        )
    ]
    scatters.extend(
        [
            go.Scatter3d(
                x=first_pos[0],
                y=first_pos[1],
                z=first_pos[2],
                opacity=0,
                marker=dict(color="blue", opacity=0),
            )
            for _ in range(ghost_count)
        ]
    )

    def update_scatters(current_index, delay, ghost_count):
        scatters[0] = go.Scatter3d(
            x=configs_dataframe[current_index][0],
            y=configs_dataframe[current_index][1],
            z=configs_dataframe[current_index][2],
            opacity=1,
            marker={
                "color": "blue",
                "opacity": 1,
            },
        )

        update_time = current_index % delay
        if update_time == 0:
            ghost_index = ((current_index - 1) // delay) % (ghost_count)
            scatters[ghost_index + 1] = go.Scatter3d(
                x=configs_dataframe[current_index][0],
                y=configs_dataframe[current_index][1],
                z=configs_dataframe[current_index][2],
                marker=dict(
                    color="blue",
                    # opacity = 1-(ghost_count-ghost_index)/ghost_count
                    # opacity=np.clip(0.6 - (ghost_count-ghost_index)/ghost_count,0.3,1)
                ),
            )

            for i in range(ghost_index, ghost_count + ghost_index):
                index = i % ghost_count
                scatters[index].mode = "lines+markers"
                scatters[index].marker = {
                    "opacity": 1 - 0.5 * index / ghost_count,
                    "color": "blue",
                    "size": 3,
                }
                scatters[index].opacity = 1 - 0.5 * index / ghost_count

        return scatters

    # last_pos = configs_dataframe[configs_dataframe.columns[5]]
    fig = go.Figure(
        data=scatters,
        layout=go.Layout(
            updatemenus=[
                dict(
                    type="buttons",
                    buttons=[
                        dict(
                            args=[
                                None,
                                {
                                    "frame": {
                                        "duration": frame_duration,
                                        "redraw": True,
                                    },
                                    "fromcurrent": True,
                                },
                            ],
                            label="Play",
                            method="animate",
                        )
                    ],
                )
            ],
            scene={
                "xaxis": dict(range=[-3, 3]),
                "yaxis": dict(range=[-3, 3]),
                "zaxis": dict(range=[-3, 3]),
                "aspectmode": "cube",
            },
            width=700,
            height=700,
        ),
        frames=[
            go.Frame(data=update_scatters(k, delay=delay, ghost_count=ghost_count))
            for k in range(1, len(configurations_dictionary))
        ],
    ).update_traces(marker=dict(size=3))

    fig.show()

In [ ]:
visualise_simulation_animation_traces(configurations, ghost_count=4, delay=20, frame_duration=20)

In [ ]:
sim.visualise_simulation_animation(configurations)

In [48]:
count = 30
length = 0.1
initial_configuration = sim.configuration_multilink_line(count=count, length=length)

iterations = 1000
dt = 0.002
T = np.arange(dt, iterations*dt+dt, dt)
# constant shift in x
dx = np.ones(iterations)*dt
# cos and sin in y and z

# OG nicesnake
# dy = np.cos(12*T)*dt
# dz = -np.sin(20*T)*dt

dy = np.cos(12*T)*dt
dz = -np.sin(20*T)*dt
long_configuration = sim.calculate_kinematics(initial_configuration, dx, dy, dz, iterations, eps=10**(-9))

In [51]:
visualise_simulation_animation_traces(long_configuration, frame_duration=20)

In [ ]:
sim.visualise_simulation_animation(long_configuration, frame_duration = 20)

In [ ]:
sim.visualise_simulation_evolution(
    configurations[20:40:5],
    count,
    range_x=(-0.5, 3.5),
    range_y=(-0.5, 3.5),
    range_z=(-1, 0.5),
    # color_disc_map=lambda val: f"rgba({255*val}, 0, {255*(1.-val)}, {(np.sin(np.abs(val*np.pi - np.pi/2))**3 + 0.3)/1.5 })", #val*0.7+0.3
    color_disc_map=lambda val: f"rgba({255*val}, 0, {255*(1.-val)}, {np.piecewise(val, [val == 0. or val == 1., val != 0 and val != 1], [1, 0.4])})"
)